# Temporal impact: machine time waste

In [1]:
import pandas
from IPython import display
import findspark
findspark.init()
import pyspark
import pyspark.sql
import sys

from pyspark.sql.functions import col, lag, when, concat_ws, last, first
from pyspark.sql import Window
from pyspark.sql.types import LongType

In [2]:
cluster="b"

In [3]:
spark = pyspark.sql.SparkSession.builder \
    .appName("machine_time_waste") \
    .getOrCreate()

df = spark.read.json("/home/claudio/google_2019/instance_events/" + cluster + "/" + cluster + "_instance_events*.json.gz")

ERROR:root:Exception while sending command.
Traceback (most recent call last):
  File "/opt/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1207, in send_command
    raise Py4JNetworkError("Answer from Java side is empty")
py4j.protocol.Py4JNetworkError: Answer from Java side is empty

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/opt/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1033, in send_command
    response = connection.send_command(command)
  File "/opt/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1212, in send_command
    "Error while receiving", e, proto.ERROR_ON_RECEIVE)
py4j.protocol.Py4JNetworkError: Error while receiving
ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:36135)
Traceback (most recent call last):
  File "/home/claudio/python-venv/lib/python3.6/site-packages/IPython/core/interactiveshell.py",

Py4JError: An error occurred while calling o26.json

In [ ]:
df.printSchema()

In [ ]:
df.show()

In [ ]:
#  .filter(df.collection_type == 0) \
df2 = df \
    .withColumn("time", col("time").cast(LongType())) \
    .withColumn("type", col("type").cast(LongType())) \
    .withColumn("type", when(col("type").isNull(), 0).otherwise(col("type"))) \
    .withColumn("id", concat_ws("-", "collection_id", "instance_index")) \
    .where(col("time").isNotNull()) \
    .where(col("type").isNotNull()) \
    .where((col("instance_index").isNotNull()) & (col("collection_id").isNotNull())) \
    .select("machine_id", "id", "time", "type")

In [ ]:
df2.show()
print("Total: " + str(df.count()))
print("Filtered: " + str(df2.count()))

In [ ]:
# my_window = Window.partitionBy("machine_id", "id").orderBy(df2.time.asc())

w2 = Window.partitionBy("id").orderBy(df2.time.asc()).rowsBetween(Window.currentRow, Window.unboundedFollowing)

In [ ]:
#     .withColumn("prev_time", lag(df2.time).over(my_window)) \
#    .withColumn("prev_type", lag(df2.type).over(my_window)) \

df3 = df2 \
    .withColumn("t3_time", when((df2.type != 3), None).otherwise(df2.time)) \
    .withColumn("t45678_time", when((df2.type < 4) | (df2.type > 8), None).otherwise(df2.time)) \
    .withColumn("t45678_type", when((df2.type < 4) | (df2.type > 8), None).otherwise(df2.type)) \
    .withColumn("t01_time", when((df2.type != 0) & (df2.type != 1), None).otherwise(df2.time)) \
    .withColumn("t01_type", when((df2.type != 0) & (df2.type != 1), None).otherwise(df2.type)) \
    .withColumn("next_time", when(df2.type == 3, first(col("t45678_time"), ignorenulls=True).over(w2)) \
                                  .when((df2.type == 0) | (df2.type == 1), first(col("t3_time"), ignorenulls=True).over(w2)) \
                                  .when((df2.type >= 4) | (df2.type <= 8), first(col("t01_time"), ignorenulls=True).over(w2)) \
                                  .otherwise(None)) \
    .withColumn("next_type", when(df2.type == 3, first(col("t45678_type"), ignorenulls=True).over(w2)) \
                                  .when((df2.type == 0) | (df2.type == 1), 3) \
                                  .when((df2.type >= 4) | (df2.type <= 8), first(col("t01_type"), ignorenulls=True).over(w2)) \
                                  .otherwise(None)) \
    .withColumn("last_term_type", last(col("t45678_type"), ignorenulls=True).over(w2)) \
    .withColumn("time_delta", col("next_time") - col("time")) \
    .select("machine_id", "id", "time", "type", "last_term_type", "time_delta", "t01_time", "t01_type", "t3_time", "t45678_time", "t45678_type", "next_time", "next_type") \

In [ ]:
df4 = df3.where(df3.next_type.isNotNull()).groupby("type", "next_type", "last_term_type").sum("time_delta")

In [ ]:
# df3.orderBy(df3.machine_id, df3.time).show(n=100)
# df3.printSchema()
df4.show(n=1000000)
df4.write.csv("/home/claudio/google_2019/thesis_queries/machine_time_waste/" + cluster + "_state_change.csv")